In [1]:
magma_dir = '/home/ubuntu/magma/'
bucket_dir = '/home/ubuntu/s3/'
transformers_dir = '/home/ubuntu/transformers/'
cache_dir = bucket_dir+'.cache/'

## **Fine-tuning**

In [2]:
finetune_script = '"'+transformers_dir+'examples/seq2seq/finetune_trainer.py"'
eval_script = '"'+transformers_dir+'examples/seq2seq/run_eval.py"'

### **Config**

In [3]:
import sys
sys.path.insert(0, magma_dir)
import config

import wandb
wandb.login()

project_name = 'ft_bart_para_wordembed'
%env WANDB_PROJECT=$project_name

Failed to query for notebook name, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable
wandb: Currently logged in as: marcoabrate (use `wandb login --relogin` to force relogin)


env: WANDB_PROJECT=ft_bart_para_wordembed


### Karger Books Para Wordembed

In [4]:
model_name_or_path = 'sshleifer/distilbart-cnn-12-6'

In [5]:
data_dir = '"'+bucket_dir+'datasets/karger_books_para_wordembed/bart/st/"'

output_dir = '"'+bucket_dir+'fine-tuning/'+project_name+'"'

log_dir = output_dir + '/logs'

In [6]:
from transformers import AutoConfig
model_config = AutoConfig.from_pretrained(model_name_or_path)
model_config.min_length = config.ONE_BULLET_MIN_LEN
model_config.max_length = config.ONE_BULLET_MAX_LEN
model_config.num_beams = 2

model_config.task_specific_params['summarization']['min_length'] = config.ONE_BULLET_MIN_LEN
model_config.task_specific_params['summarization']['max_length'] = config.ONE_BULLET_MAX_LEN
model_config.task_specific_params['summarization']['num_beams'] = 2
model_config_dir = '"'+bucket_dir+'fine-tuning/'+\
    model_name_or_path.replace('/', '?')+'_config"'
model_config.save_pretrained(model_config_dir[1:-1])

##### Fine tune

In [7]:
'''
model_name_or_path = output_dir[:-1] + 'checkpoint-325"'
print(model_name_or_path)

from transformers import AutoTokenizer
tok = AutoTokenizer.from_pretrained('sshleifer/distilbart-cnn-12-6', use_cache=False)
tok.save_pretrained(model_name_or_path[1:-1])
'''

'\nmodel_name_or_path = output_dir[:-1] + \'checkpoint-325"\'\nprint(model_name_or_path)\n\nfrom transformers import AutoTokenizer\ntok = AutoTokenizer.from_pretrained(\'sshleifer/distilbart-cnn-12-6\', use_cache=False)\ntok.save_pretrained(model_name_or_path[1:-1])\n'

In [8]:
!python3 $finetune_script \
--model_name_or_path $model_name_or_path \
--config_name $model_config_dir \
--tokenizer_name $model_name_or_path \
--cache_dir $cache_dir \
--data_dir $data_dir \
--freeze_embeds \
--do_train \
--learning_rate 5e-5 \
--label_smoothing_factor 0.1 \
--warmup_steps 0 \
--fp16 \
--sortish_sampler \
--task summarization \
--max_source_length 1024 \
--max_target_length $config.ONE_BULLET_MAX_LEN \
--val_max_target_length $config.ONE_BULLET_MAX_LEN \
--num_train_epochs 20 \
--logging_steps 7 --logging_first_step \
--per_device_train_batch_size 2 --per_device_eval_batch_size 8 \
--gradient_accumulation_steps 16 \
--evaluation_strategy steps --eval_steps 7 --eval_beams 2 \
--predict_with_generate \
--save_steps 98 \
--output_dir $output_dir \
--overwrite_output_dir \
--seed $config.SEED \
--run_name $output_dir

02/16/2021 09:28:05 - WARNING - __main__ -   Process rank: -1, device: cuda:0, n_gpu: 1, distributed training: False, 16-bits training: True
02/16/2021 09:28:05 - INFO - __main__ -   Training/evaluation parameters Seq2SeqTrainingArguments(output_dir='/home/ubuntu/s3/fine-tuning/ft_bart_para_wordembed', overwrite_output_dir=True, do_train=True, do_eval=None, do_predict=False, evaluation_strategy=<EvaluationStrategy.STEPS: 'steps'>, prediction_loss_only=False, per_device_train_batch_size=2, per_device_eval_batch_size=8, per_gpu_train_batch_size=None, per_gpu_eval_batch_size=None, gradient_accumulation_steps=16, eval_accumulation_steps=None, learning_rate=5e-05, weight_decay=0.0, adam_beta1=0.9, adam_beta2=0.999, adam_epsilon=1e-08, max_grad_norm=1.0, num_train_epochs=20.0, max_steps=-1, lr_scheduler_type=<SchedulerType.LINEAR: 'linear'>, warmup_steps=0, logging_dir='runs/Feb16_09-28-05_ip-172-31-39-35', logging_first_step=True, logging_steps=7, save_steps=98, save_total_limit=None, no_cu

[INFO|modeling_utils.py:1143] 2021-02-16 09:28:35,965 >> All model checkpoint weights were used when initializing BartForConditionalGeneration.

[INFO|modeling_utils.py:1152] 2021-02-16 09:28:35,965 >> All the weights of BartForConditionalGeneration were initialized from the model checkpoint at sshleifer/distilbart-cnn-12-6.
If your task is similar to the task the model of the checkpoint was trained on, you can already use BartForConditionalGeneration for predictions without further training.
02/16/2021 09:28:35 - INFO - utils -   setting model.config to task specific params for summarization:
 {'early_stopping': True, 'length_penalty': 2.0, 'max_length': 150, 'min_length': 10, 'no_repeat_ngram_size': 3, 'num_beams': 2}
02/16/2021 09:28:35 - INFO - utils -   note: command line args may override some of these
[INFO|trainer.py:348] 2021-02-16 09:28:40,150 >> Using amp fp16 backend
02/16/2021 09:28:40 - INFO - __main__ -   *** Train ***
/home/ubuntu/transformers/src/transformers/trainer.p

Batches: 100%|██████████| 1/1 [00:00<00:00, 134.74it/s]


Batches: 100%|██████████| 1/1 [00:00<00:00, 128.39it/s]


Batches: 100%|██████████| 1/1 [00:00<00:00, 138.44it/s]


...

02/16/2021 12:25:30 - INFO - gensim.models.base_any2vec -   worker thread finished; awaiting finish of 2 more threads
02/16/2021 12:25:30 - INFO - gensim.models.base_any2vec -   worker thread finished; awaiting finish of 1 more threads
02/16/2021 12:25:30 - INFO - gensim.models.base_any2vec -   worker thread finished; awaiting finish of 0 more threads
02/16/2021 12:25:30 - INFO - gensim.models.base_any2vec -   EPOCH - 1 : training on 12854 raw words (9883 effective words) took 0.0s, 205466 effective words/s
02/16/2021 12:25:30 - INFO - gensim.models.base_any2vec -   worker thread finished; awaiting finish of 2 more threads
02/16/2021 12:25:30 - INFO - gensim.models.base_any2vec -   worker thread finished; awaiting finish of 1 more threads
02/16/2021 12:25:30 - INFO - gensim.models.base_any2vec -   worker thread finished; awaiting finish of 0 more threads
02/16/2021 12:25:30 - INFO - gensim.models.base_any2vec -   EPOCH - 2 : training on 12854 raw words (9927 effective words) took 0.0s,

Batches: 100%|██████████| 1/1 [00:00<00:00, 132.86it/s]


Batches: 100%|██████████| 1/1 [00:00<00:00, 132.05it/s]


Batches: 100%|██████████| 1/1 [00:00<00:00, 134.13it/s]


Batches: 100%|██████████| 1/1 [00:00<00:00, 124.92it/s]
02/16/2021 12:26:43 - INFO - gensim.models.word2vec -   collecting all words and their counts
02/16/2021 12:26:43 - INFO - gensim.models.word2vec -   PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
02/16/2021 12:26:43 - INFO - gensim.models.word2vec -   collected 2722 word types from a corpus of 12710 raw words and 532 sentences
02/16/2021 12:26:43 - INFO - gensim.models.word2vec -   Loading a fresh vocabulary
02/16/2021 12:26:43 - INFO - gensim.models.word2vec -   effective_min_count=1 retains 2722 unique words (100% of original 2722, drops 0)
02/16/2021 12:26:43 - INFO - gensim.models.word2vec -   effective_min_count=1 leaves 12710 word corpus (100% of original 12710, drops 0)
02/16/2021 12:26:43 - INFO - gensim.models.word2vec -   deleting the raw counts dictionary of 2722 items
02/16/2021 12:26:43 - INFO - gensim.models.word2vec -   sample=0.001 downsamples 33 most-common words
02/16/2021 12:26:43 - INFO - ge